In [ ]:
import numpy as np
import pandas as pd 
import matplotlib.pyplot as plt

%matplotlib inline

# _______________________________________

# Kernels Data (Public Score & File Path)

dfk = pd.DataFrame({ 
    'Kernel ID': ['A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J', 'K', 'L', 'M'],  
    'Score':     [14.763, 13.168, 11.600, 10.959, 9.773, 9.530, 8.500, 8.418, 8.333, 8.309, 8.073, 7.745, 7.661],   
    'File Path': ['../input/indoor14763/Indoor14763.csv', '../input/indoor13168/Indoor13168.csv', '../input/indoor11600/Indoor11600.csv', '../input/indoor10959/Indoor10959.csv', '../input/indoor9773/Indoor9773.csv', '../input/indoor9530/Indoor9530.csv', '../input/indoor8500/Indoor8500.csv', '../input/indoor8418/Indoor8418.csv', '../input/indoor8333/Indoor8333.csv', '../input/indoor8309/Indoor8309.csv', '../input/indoor8073/Indoor8073.csv', '../input/indoornav7745sub/submission.csv', '../input/indoor7661/Indoor7661.csv']     
})    
    
dfk   

# Ensembling & Comparative Method

In [ ]:
ff1x = 0.50   # Hyperparameter
ff1y = 0.50   # Hyperparameter

ff2x = 0.95   # Hyperparameter
ff2y = 0.95   # Hyperparameter

ff3x = 0.90   # Hyperparameter
ff3y = 0.90   # Hyperparameter

main = pd.read_csv(dfk.iloc[12, 2]) 
support = pd.read_csv(dfk.iloc[11, 2])

rx , ry = [] , []
generated  = main.copy()  

mx , my , mz = [] , [] , []
mx = main.iloc[:, 2].tolist()
my = main.iloc[:, 3].tolist()
mz = main.iloc[:, 1].tolist()

sx , sy = [] , []
sx = support.iloc[:, 2].tolist()
sy = support.iloc[:, 3].tolist()

kx = [[],[],[],[],[],[],[],[],[],[],[]]
ky = [[],[],[],[],[],[],[],[],[],[],[]]
for n in range (11):
    kernel   = pd.read_csv(dfk.iloc[n, 2])  
    kx[n] = kernel.iloc[:, 2].tolist()
    ky[n] = kernel.iloc[:, 3].tolist()

for j in range(len(main)):
    
    ex = (mx[j] * ff1x) + (sx[j] * (1.- ff1x))
    ey = (my[j] * ff1y) + (sy[j] * (1.- ff1y))
    
    if (mx[j] >= sx[j]):
        a = mx[j]
        b = sx[j]
    else: 
        a = sx[j]
        b = mx[j]
        
    if (my[j] >= sy[j]):
        c = my[j]
        d = sy[j]
    else: 
        c = sy[j]
        d = my[j]    

    for k in range (5):            
        if ((b <= kx[k][j] <= a) and (d <= ky[k][j] <= c)):
            
            ex = (ex * ff2x) + (kx[k][j] * (1.- ff2x))
            ey = (ey * ff2y) + (ky[k][j] * (1.- ff2y))
            
            print(f'Row:{j}\t Kernel Number:{k}\t Floor:{mz[j]}')
            print(f'Main:({mx[j]},{my[j]})\nSupport:({sx[j]},{sy[j]})\nKernel:({kx[k][j]},{ky[k][j]})\nResult:({ex},{ey})\n')
            
    for k in range (5, 11):            
        if ((b <= kx[k][j] <= a) and (d <= ky[k][j] <= c)):
            
            ex = (ex * ff3x) + (kx[k][j] * (1.- ff3x))
            ey = (ey * ff3y) + (ky[k][j] * (1.- ff3y))
            
            print(f'Row:{j}\t Kernel Number:{k}\t Floor:{mz[j]}')
            print(f'Main:({mx[j]},{my[j]})\nSupport:({sx[j]},{sy[j]})\nKernel:({kx[k][j]},{ky[k][j]})\nResult:({ex},{ey})\n')            
            
    rx.append(ex)
    ry.append(ey)    

generated.iloc[:, 2] = rx
generated.iloc[:, 3] = ry


Row:0	 Kernel Number:3	 Floor:0
Main:(88.2500228881836,102.6282958984375)
Support:(93.33883384291568,100.57223051022952)
Kernel:(93.06026095415235,102.38296435591911)
Result:(90.90771999497977,101.63939826191279)

Row:2	 Kernel Number:8	 Floor:0
Main:(79.1816635131836,105.39734649658205)
Support:(90.03739432301464,105.51865977259556)
Kernel:(88.09556275891174,105.40257230360912)
Result:(84.95813230218037,105.45246005149083)

Row:5	 Kernel Number:7	 Floor:0
Main:(83.17462921142578,108.21607971191406)
Support:(81.93328671533008,110.09860890092295)
Kernel:(82.40186518675063,108.69723891627144)
Result:(82.5387486857152,109.1113337674038)

Row:6	 Kernel Number:9	 Floor:0
Main:(85.21501922607422,109.28977966308594)
Support:(84.17431165472924,106.57368148867376)
Kernel:(84.39017938395969,107.10945141994227)
Result:(84.66421683475753,107.84950266028609)

Row:6	 Kernel Number:10	 Floor:0
Main:(85.21501922607422,109.28977966308594)
Support:(84.17431165472924,106.57368148867376)
Kernel:(84.390179

<div class="alert alert-success">  
</div>

In [ ]:
import json
import matplotlib.pylab as plt


In [ ]:
def split_col(df):
    """
    Split submission site/path/timestamp into individual columns.
    """
    df = pd.concat(
        [
            df["site_path_timestamp"]
            .str.split("_", expand=True)
            .rename(columns={0: "site", 1: "path", 2: "timestamp"}),
            df,
        ],
        axis=1,
    ).copy()
    return df


def plot_preds(
    site,
    floorNo,
    sub=None,
    true_locs=None,
    base="../input/indoor-location-navigation",
    show_train=True,
    show_preds=True,
):
    """
    Plots predictions on floorplan map.
    """
    # Prepare width_meter & height_meter (taken from the .json file)
    floor_plan_filename = f"{base}/metadata/{site}/{floorNo}/floor_image.png"
    json_plan_filename = f"{base}/metadata/{site}/{floorNo}/floor_info.json"
    with open(json_plan_filename) as json_file:
        json_data = json.load(json_file)

    width_meter = json_data["map_info"]["width"]
    height_meter = json_data["map_info"]["height"]

    floor_img = plt.imread(f"{base}/metadata/{site}/{floorNo}/floor_image.png")

    fig, ax = plt.subplots(figsize=(12, 12))
    plt.imshow(floor_img)

    if show_train:
        true_locs["x_"] = true_locs["x"] * floor_img.shape[0] / height_meter
        true_locs["y_"] = (
            true_locs["y"] * -1 * floor_img.shape[1] / width_meter
        ) + floor_img.shape[0]
        true_locs.query("site == @site and floorNo == @floorNo").groupby("path").plot(
            x="x_",
            y="y_",
            style="+",
            ax=ax,
            label="train waypoint location",
            color="grey",
            alpha=0.5,
        )

    if show_preds:
        sub["x_"] = sub["x"] * floor_img.shape[0] / height_meter
        sub["y_"] = (
            sub["y"] * -1 * floor_img.shape[1] / width_meter
        ) + floor_img.shape[0]
        for path, path_data in sub.query(
            "site == @site and floorNo == @floorNo"
        ).groupby("path"):
            path_data.plot(
                x="x_",
                y="y_",
                style=".-",
                ax=ax,
                title=f"{site} - floor - {floorNo}",
                alpha=1,
                label=path,
            )
    return fig, ax


In [ ]:
sub = split_col(generated)

true_locs = pd.read_csv("../input/indoor-location-train-waypoints/train_waypoints.csv")

# Add floor No to sub file
sub = sub.merge(true_locs[["site", "floor", "floorNo"]].drop_duplicates())


for (site, floorNo), d in sub.groupby(["site", "floorNo"]):
    fig, ax = plot_preds(site, floorNo, sub, true_locs)
    # Remove duplicate labels
    handles, labels = ax.get_legend_handles_labels()
    by_label = dict(zip(labels, handles))
    plt.legend(
        by_label.values(), by_label.keys(), loc="center left", bbox_to_anchor=(1, 0.5)
    )
    plt.show()
    

<div class="alert alert-success">  
</div>

<div class="alert alert-success">  
</div>